In [1]:
import numpy as np
import pandas
import pm4py
from matplotlib import pyplot as plt
from sklearn.mixture import GaussianMixture
import scipy.stats as stats
import ot
import os
from tqdm import tqdm
import collections
import matplotlib.dates as md
import importlib
import pickle
import random
import math
import CRPS.CRPS as pscore
import datetime

pandas.set_option('display.max_columns', None)
#pandas.set_option('display.max_rows', None)


import sys
sys.path.append('../../TaskExecutionTimeMining/')
from drbart_parser import *
from event_log_transformer import *

#sys.path.append('../../Evaluation')
sys.path.append('../../Evaluation/')
from normal_evaluation.drbart_evaluation import *

In [2]:
model_name = 'artificial_2'
log_name = 'train'
with open('../transformed_event_logs/artificial_start_end_2_'+log_name+'.pickle', 'rb') as f:
    test_event_log = pickle.load(f)

#test_event_log['time:timestamp'] = test_event_log['time:timestamp_complete']
test_event_log['case:concept:name'] = test_event_log['case:concept:name'].astype(str)
known_resources = ['1', 'Clark', 'Jane', 'Joe', 'Karsten']
known_activities = ['DIAGNOSIS', 'QUALITY_CONTROL', 'REPAIR']

In [3]:
test_event_log

concept:name lifecycle:transition_start  \
0           DIAGNOSIS                      START   
1              REPAIR                      START   
3           DIAGNOSIS                      START   
4              REPAIR                      START   
5     QUALITY_CONTROL                      START   
...               ...                        ...   
5400        DIAGNOSIS                      START   
5399  QUALITY_CONTROL                      START   
5401           REPAIR                      START   
5402  QUALITY_CONTROL                      START   
5403        DIAGNOSIS                      START   

                 time:timestamp_start org:resource case:concept:name  \
0    2020-01-01 03:57:40.044121+00:00         Jane                 0   
1    2020-01-01 04:34:23.549454+00:00          Joe                 0   
3    2020-01-01 08:16:35.844753+00:00         Jane                 1   
4    2020-01-01 08:47:14.772217+00:00      Karsten                 1   
5    2020-01-01 13:27:22.316694+00:00        Clark                 1   
...                               ...          ...               ...   
5400 2024-12-26 18:05:59.540931+00:00        Clark              1800   
5399 2024-12-26 19:03:41.622915+00:00          Joe              1799   
5401 2024-12-26 19:13:26.892809+00:00        Clark              1800   
5402 2024-12-27 08:23:46.946760+00:00         Jane              1800   
5403 2024-12-29 20:55:45.405475+00:00          Joe              1801   

      id_start lifecycle:transition_complete          time:timestamp_complete  \
0            1                      COMPLETE 2020-01-01 04:34:23.549454+00:00   
1            4                      COMPLETE 2020-01-01 14:30:27.423999+00:00   
3           10                      COMPLETE 2020-01-01 08:47:14.772217+00:00   
4           13                      COMPLETE 2020-01-01 13:27:22.316694+00:00   
5           16                      COMPLETE 2020-01-01 17:21:42.825766+00:00   
...        ...                           ...                              ...   
5400     16201                      COMPLETE 2024-12-26 19:13:26.892809+00:00   
5399     16198                      COMPLETE 2024-12-26 21:39:17.312456+00:00   
5401     16204                      COMPLETE 2024-12-27 08:23:46.946760+00:00   
5402     16207                      COMPLETE 2024-12-27 11:10:44.009123+00:00   
5403     16210                      COMPLETE 2024-12-29 22:15:50.349701+00:00   

      id_complete               duration  duration_seconds  seconds_in_day  \
0               2 0 days 00:36:43.505333              2203           14260   
1               5 0 days 09:56:03.874545             35763           16463   
3              11 0 days 00:30:38.927464              1838           29795   
4              14 0 days 04:40:07.544477             16807           31634   
5              17 0 days 03:54:20.509072             14060           48442   
...           ...                    ...               ...             ...   
5400        16202 0 days 01:07:27.351878              4047           65159   
5399        16199 0 days 02:35:35.689541              9335           68621   
5401        16205 0 days 13:10:20.053951             47420           69206   
5402        16208 0 days 02:46:57.062363             10017           30226   
5403        16211 0 days 01:20:04.944226              4804           75345   

      DIAGNOSIS  QUALITY_CONTROL  REPAIR  1  Clark  Jane  Joe  Karsten  
0             1                0       0  0      0     1    0        0  
1             1                0       1  0      0     1    1        0  
3             1                0       0  0      0     1    0        0  
4             1                0       1  0      0     1    0        1  
5             1                1       1  0      1     1    0        1  
...         ...              ...     ... ..    ...   ...  ...      ...  
5400          1                0       0  0      1     0    0        0  
5399          1          

In [4]:
N = 10000
n_processes = 10
import conduct_evaluation
get_pscores = lambda likelihoods : [pscore(likelihoods[1][i], likelihoods[2][k][3]).compute()[0] for i, k in enumerate(list(likelihoods[0].keys()))]

In [5]:
drbart_model_A = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name/',
                     strict_parser=True)
evaluator_A = conduct_evaluation.ConductEvaluation(drbart_model_A, SampleOutcomes_DRBART_Normal_A,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A = evaluator_A.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:38<19:15:02, 38.48s/it]

  0%|                                                                  | 2/1802 [00:38<8:04:19, 16.14s/it]

  0%|▏                                                                 | 4/1802 [00:39<3:02:05,  6.08s/it]

  0%|▏                                                                 | 5/1802 [00:39<2:07:14,  4.25s/it]

...

 99%|████████████████████████████████████████████████████████████████▋| 1792/1802 [01:38<00:00, 20.63it/s]

100%|████████████████████████████████████████████████████████████████▋| 1795/1802 [01:38<00:00, 18.66it/s]

100%|████████████████████████████████████████████████████████████████▊| 1798/1802 [01:38<00:00, 17.26it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 20.33it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.24it/s]

In [6]:
np.mean([v.ln() for v in likelihoods_A[0].values()])

Decimal('0.1339312564841888252122342548')

In [7]:
np.mean(get_pscores(likelihoods_A))

np.float64(12474.249207787943)

In [8]:
drbart_model_A_R = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource/',
                     strict_parser=True)
evaluator_A_R = conduct_evaluation.ConductEvaluation(drbart_model_A_R, SampleOutcomes_DRBART_Normal_A_R,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A_R = evaluator_A_R.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:29<14:41:43, 29.37s/it]

  0%|                                                                  | 2/1802 [00:29<6:06:25, 12.21s/it]

  0%|                                                                  | 3/1802 [00:30<3:26:40,  6.89s/it]

  0%|▏                                                                 | 5/1802 [00:30<1:31:06,  3.04s/it]

...

 99%|████████████████████████████████████████████████████████████████▌| 1790/1802 [01:37<00:00, 20.28it/s]

100%|████████████████████████████████████████████████████████████████▋| 1793/1802 [01:37<00:00, 19.07it/s]

100%|████████████████████████████████████████████████████████████████▊| 1796/1802 [01:37<00:00, 17.44it/s]

100%|████████████████████████████████████████████████████████████████▉| 1800/1802 [01:37<00:00, 20.03it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.36it/s]

In [9]:
np.mean([v.ln() for v in likelihoods_A_R[0].values()])

Decimal('0.2346412839104646916243800171')

In [10]:
np.mean(get_pscores(likelihoods_A_R))

np.float64(10619.139164680399)

In [11]:
drbart_model_R_S = DRBART(parser_dir = '../../../models/'+model_name+'/resource_seconds-in-day/',
                     strict_parser=True)
evaluator_R_S = conduct_evaluation.ConductEvaluation(drbart_model_R_S, SampleOutcomes_DRBART_Normal_R_S,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R_S = evaluator_R_S.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:41<20:52:52, 41.74s/it]

  0%|                                                                  | 2/1802 [00:43<8:58:45, 17.96s/it]

  1%|▎                                                                | 10/1802 [00:43<1:11:01,  2.38s/it]

  1%|▍                                                                | 11/1802 [01:23<3:41:09,  7.41s/it]

...

 99%|████████████████████████████████████████████████████████████████▋| 1792/1802 [01:38<00:00, 19.24it/s]

100%|████████████████████████████████████████████████████████████████▊| 1797/1802 [01:39<00:00, 18.62it/s]

100%|████████████████████████████████████████████████████████████████▉| 1799/1802 [01:39<00:00, 17.47it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:39<00:00, 19.62it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:39<00:00, 18.11it/s]

In [12]:
np.mean([v.ln() for v in likelihoods_R_S[0].values()])

Decimal('-0.2253426367326515807251465719')

In [13]:
np.mean(get_pscores(likelihoods_R_S))

np.float64(19681.548699827945)

In [14]:
drbart_model_R = DRBART(parser_dir = '../../../models/'+model_name+'/resource/',
                     strict_parser=True)
evaluator_R = conduct_evaluation.ConductEvaluation(drbart_model_R, SampleOutcomes_DRBART_Normal_R,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_R = evaluator_R.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:46<23:27:50, 46.90s/it]

  0%|                                                                  | 2/1802 [00:47<9:53:40, 19.79s/it]

  0%|▏                                                                 | 4/1802 [00:48<3:53:18,  7.79s/it]

  1%|▍                                                                | 11/1802 [01:34<3:22:06,  6.77s/it]

...

 99%|████████████████████████████████████████████████████████████████▍| 1788/1802 [01:37<00:00, 18.50it/s]

100%|████████████████████████████████████████████████████████████████▋| 1793/1802 [01:37<00:00, 18.92it/s]

100%|████████████████████████████████████████████████████████████████▋| 1795/1802 [01:37<00:00, 17.08it/s]

100%|████████████████████████████████████████████████████████████████▊| 1798/1802 [01:38<00:00, 18.73it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.37it/s]

In [15]:
np.mean([v.ln() for v in likelihoods_R[0].values()])

Decimal('-0.1486198019229477949385336931')

In [16]:
np.mean(get_pscores(likelihoods_R))

np.float64(17454.023853625164)

In [17]:
drbart_model_A_R_S = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day/',
                     strict_parser=True)
evaluator_A_R_S = conduct_evaluation.ConductEvaluation(drbart_model_A_R_S, SampleOutcomes_DRBART_Normal_A_R_S,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A_R_S = evaluator_A_R_S.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:30<15:04:36, 30.14s/it]

  0%|                                                                  | 2/1802 [00:30<6:21:38, 12.72s/it]

  0%|                                                                  | 3/1802 [00:30<3:30:42,  7.03s/it]

  0%|▎                                                                   | 7/1802 [00:31<59:00,  1.97s/it]

...

100%|████████████████████████████████████████████████████████████████▋| 1795/1802 [01:37<00:00, 18.85it/s]

100%|████████████████████████████████████████████████████████████████▊| 1797/1802 [01:37<00:00, 17.96it/s]

100%|████████████████████████████████████████████████████████████████▉| 1800/1802 [01:38<00:00, 18.84it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.04it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.35it/s]

In [18]:
np.mean([v.ln() for v in likelihoods_A_R_S[0].values()])

Decimal('0.2065186387050332130063821413')

In [19]:
np.mean(get_pscores(likelihoods_A_R_S))

np.float64(11880.269792946372)

In [20]:
drbart_model_A_R_S_AC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_activity-count/',
                     strict_parser=True)
evaluator_A_R_S_AC = conduct_evaluation.ConductEvaluation(drbart_model_A_R_S_AC, SampleOutcomes_DRBART_Normal_A_R_S_AC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A_R_S_AC = evaluator_A_R_S_AC.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:26<13:29:32, 26.97s/it]

  0%|                                                                  | 2/1802 [00:27<5:35:25, 11.18s/it]

  0%|▏                                                                 | 5/1802 [00:27<1:36:55,  3.24s/it]

  0%|▎                                                                   | 8/1802 [00:27<49:08,  1.64s/it]

...

 99%|████████████████████████████████████████████████████████████████▍| 1788/1802 [01:37<00:00, 19.96it/s]

 99%|████████████████████████████████████████████████████████████████▋| 1792/1802 [01:38<00:00, 16.34it/s]

100%|████████████████████████████████████████████████████████████████▋| 1795/1802 [01:38<00:00, 17.27it/s]

100%|████████████████████████████████████████████████████████████████▉| 1800/1802 [01:38<00:00, 22.18it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.23it/s]

In [21]:
np.mean([v.ln() for v in likelihoods_A_R_S_AC[0].values()])

Decimal('0.2985323696778887933536145347')

In [22]:
np.mean(get_pscores(likelihoods_A_R_S_AC))

np.float64(9987.473630911254)

In [23]:
drbart_model_A_R_S_RC_AC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_activity-count_resource-count/',
                     strict_parser=True)
evaluator_A_R_S_RC_AC = conduct_evaluation.ConductEvaluation(drbart_model_A_R_S_RC_AC, SampleOutcomes_DRBART_Normal_A_R_S_RC_AC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                        'known_resources' : known_resources,
                                                        'known_activities' : known_activities,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A_R_S_RC_AC = evaluator_A_R_S_RC_AC.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:27<13:50:59, 27.68s/it]

  0%|                                                                  | 3/1802 [00:27<3:36:43,  7.23s/it]

  0%|▏                                                                 | 5/1802 [00:28<1:47:56,  3.60s/it]

  0%|▎                                                                 | 7/1802 [00:28<1:02:53,  2.10s/it]

...

 99%|████████████████████████████████████████████████████████████████▌| 1790/1802 [01:37<00:00, 21.36it/s]

100%|████████████████████████████████████████████████████████████████▋| 1793/1802 [01:37<00:00, 16.56it/s]

100%|████████████████████████████████████████████████████████████████▊| 1796/1802 [01:37<00:00, 18.33it/s]

100%|████████████████████████████████████████████████████████████████▉| 1800/1802 [01:38<00:00, 21.68it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.31it/s]

In [24]:
np.mean([v.ln() for v in likelihoods_A_R_S_RC_AC[0].values()])

Decimal('0.3073106169658189100163599048')

In [25]:
np.mean(get_pscores(likelihoods_A_R_S_RC_AC))

np.float64(10342.889932291033)

In [26]:
drbart_model_A_R_S_RC = DRBART(parser_dir = '../../../models/'+model_name+'/concept-name_resource_seconds-in-day_resource-count/',
                     strict_parser=True)
evaluator_A_R_S_RC = conduct_evaluation.ConductEvaluation(drbart_model_A_R_S_RC, SampleOutcomes_DRBART_Normal_A_R_S_RC,
                                                   {
                                                        'activity_key' : 'concept:name',
                                                        'resource_key' : 'org:resource',
                                                        'known_resources' : known_resources,
                                                    },
                                     test_event_log, n=N, n_processes=n_processes)
likelihoods_A_R_S_RC = evaluator_A_R_S_RC.sample_cases(False, True)

  0%|                                                                            | 0/1802 [00:00<?, ?it/s]

  0%|                                                                 | 1/1802 [00:23<11:43:40, 23.44s/it]

  0%|                                                                  | 3/1802 [00:23<3:04:43,  6.16s/it]

  0%|▏                                                                 | 4/1802 [00:23<2:02:27,  4.09s/it]

  0%|▏                                                                 | 5/1802 [00:24<1:23:35,  2.79s/it]

...

 99%|████████████████████████████████████████████████████████████████▋| 1792/1802 [01:37<00:00, 16.65it/s]

100%|████████████████████████████████████████████████████████████████▊| 1796/1802 [01:37<00:00, 20.82it/s]

100%|████████████████████████████████████████████████████████████████▉| 1799/1802 [01:38<00:00, 18.23it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 16.58it/s]

100%|█████████████████████████████████████████████████████████████████| 1802/1802 [01:38<00:00, 18.33it/s]

In [27]:
np.mean([v.ln() for v in likelihoods_A_R_S_RC[0].values()])

Decimal('0.1896519581471551559921572265')

In [28]:
np.mean(get_pscores(likelihoods_A_R_S_RC))

np.float64(12499.048253084147)

In [29]:
results = {
    'drbart_model_A' : likelihoods_A,
    'drbart_model_A_R' : likelihoods_A_R,
    'drbart_model_R' : likelihoods_R,
    'drbart_model_R_S' : likelihoods_R_S,
    'drbart_model_A_R_S' : likelihoods_A_R_S,
    'drbart_model_A_R_S_AC' : likelihoods_A_R_S_AC,
    'drbart_model_A_R_S_RC' : likelihoods_A_R_S_RC,
    'drbart_model_A_R_S_RC_AC' : likelihoods_A_R_S_RC_AC
}

with open('./'+model_name+'_dr_bart_evaluation_'+log_name+'.pickle', 'wb') as handle:
    pickle.dump(results, handle)